In [1]:
import pandas
import xml.etree.ElementTree as ET
import os
import csv
import re
%matplotlib inline
import numpy as np
import pandas as pd
import librosa as lb
import librosa.display
import matplotlib.pyplot as plt
from gensim.models import Word2Vec

In [2]:
def read_csv(file_name):
    file = open(file_name)
    df = pandas.read_csv(file_name)
    return df

    

In [3]:
def read_bml(file_name):
    tree = ET.parse(file_name)
    root = tree.getroot()
    return root
    

In [4]:
def read_viseme(root):
    viseme_l = list()
    for child in root:
        viseme = list()
#         print(child.tag)
        if(child.tag == "lips"):
#             print(True)
            viseme.append(child.attrib['viseme'])
            viseme.append(child.attrib['start'])
            viseme.append(child.attrib['end'])
            viseme_l.append(viseme)
    return viseme_l
            

In [5]:
def read_transcript(root,end_time):
    for child in root:
        if(child.tag=='speech'):
            for child2 in child:
                if(child2.tag == 'text'):
                    texttag = child2
                    break
    transcript_l = list()
    next_t =0
    for i,sync in enumerate(texttag):
        transcript = list()
        for t in sync:
            print(t)
        if sync.text is None : 
            transcript.append('000')
        else:    
            transcript.append(sync.text)
#         transcript.append(prev)
        transcript.append(sync.attrib['time'])
        if(i<len(texttag)-1):
            transcript.append(texttag[i+1].attrib['time'])
        else:
            transcript.append(end_time)
        
        prev = sync.attrib['time']
        transcript_l.append(transcript)
    return transcript_l

In [62]:
viseme_set = list()
transcript_set = list()
viseme_feature_set = list()

In [50]:
for i, elem in enumerate(transcript_set):
    s = textual_features(transcript_set[i],viseme_set[i])
    viseme_text_features.append(s)


In [51]:
viseme_text_features

[[('_', '000', '0', '0.48'),
  ('Ih', 'Excuse ', '0.48', '0.51'),
  ('Kg', 'Excuse ', '0.51', '0.52'),
  ('Z', 'Excuse ', '0.52', '0.61'),
  ('Kg', 'Excuse ', '0.61', '0.68'),
  ('Sh', 'Excuse ', '0.68', '0.72'),
  ('W', 'Excuse ', '0.72', '0.78'),
  ('Z', 'Excuse ', '0.78', '0.8'),
  ('BMP', 'me', '0.8', '0.86'),
  ('Ih', 'me', '0.86', '1.09'),
  ('_', '000', '1.09', '1.945562')],
 [('_', '000', '0', '0.51'),
  ('Sh', 'Yeah', '0.51', '0.64'),
  ('Ah', 'Yeah', '0.64', '0.85'),
  ('_', '000', '0.85', '1.382437')],
 [('_', '000', '0', '0.33'),
  ('Ih', 'Is', '0.33', '0.36'),
  ('Z', 'Is', '0.36', '0.52'),
  ('_', '000', '0.52', '2.11'),
  ('Th', 'there', '2.11', '2.21'),
  ('Er', 'there', '2.21', '2.29'),
  ('Ah', 'a', '2.29', '2.32'),
  ('BMP', 'problem', '2.32', '2.36'),
  ('R', 'problem', '2.36', '2.45'),
  ('Aa', 'problem', '2.45', '2.57'),
  ('BMP', 'problem', '2.57', '2.58'),
  ('L', 'problem', '2.58', '2.63'),
  ('Ah', 'problem', '2.63', '2.69'),
  ('BMP', 'problem', '2.69', '2.88

In [ ]:
viseme_text_features

[[('_', '000', '0', '0.29'),
  ('H', 'Hmm', '0.29', '0.36'),
  ('Ah', 'Hmm', '0.36', '0.46'),
  ('BMP', 'Hmm', '0.46', '0.56'),
  ('_', '000', '0.56', '1.75')],
 [('_', '000', '0', '1.2'),
  ('Ah', 'I', '1.2', '1.285'),
  ('Ih', 'I', '1.285', '1.37'),
  ('Aa', 'almost', '1.37', '1.4'),
  ('L', 'almost', '1.4', '1.43'),
  ('BMP', 'almost', '1.43', '1.49'),
  ('Ow', 'almost', '1.49', '1.59'),
  ('Z', 'almost', '1.59', '1.69'),
  ('D', 'almost', '1.69', '1.71'),
  ('Kg', 'got', '1.71', '1.73'),
  ('Aa', 'got', '1.73', '1.83'),
  ('D', 'got', '1.83', '1.84'),
  ('BMP', 'married', '1.84', '1.92'),
  ('Ah', 'married', '1.92', '2.06'),
  ('R', 'married', '2.06', '2.08'),
  ('Ih', 'married', '2.08', '2.16'),
  ('D', 'married', '2.16', '2.17'),
  ('D', 'two', '2.17', '2.32'),
  ('W', 'two', '2.32', '2.39'),
  ('Sh', 'years', '2.39', '2.44'),
  ('Ih', 'years', '2.44', '2.52'),
  ('R', 'years', '2.52', '2.56'),
  ('Z', 'years', '2.56', '2.73'),
  ('_', '000', '2.73', '2.79'),
  ('Ah', 'ago', '2.7

In [ ]:
sentences = []
for filename in os.listdir(read_viseme_mod):
    file_path_read = os.path.join(read_viseme_mod, filename)
#     print(file_path_read)
    f_r = open(file_path_read,'r+')
    root = read_bml(f_r)
    script = read_transcript(root,0)
    sent = []
    for data in script :
        sent.append(data[0])
    sentences.append(sent)

In [ ]:
model = Word2Vec(sentences, min_count=1,vector_size= 50,workers=3)                 
model.save("word2vec.model")       


In [52]:
model = Word2Vec.load("word2vec.model")

In [17]:
vocabulary = model.wv.key_to_index

In [64]:
def create_mfcc(audio_path, start_ms, end_ms):
    start = start_ms/100
    end = end_ms/100
    y, sr = librosa.load(audio_path,sr=28000)
    y_cut = y[round(start*sr,ndigits=None)
         :round(end*sr, ndigits= None)]
    try:
        data = np.array([padding(librosa.feature.mfcc(y_cut,
             n_fft=n_fft,hop_length=hop_length,n_mfcc=128),128,50)])
    except:
        data = librosa.feature.mfcc(y_cut,
             n_fft=n_fft,hop_length=hop_length,n_mfcc=128)
        data = np.array([data[:, :50]])
    #data, sample_rate = lb.load(audio_path, offset = start, duration = end - start)
#     lb.display.waveplot(data)
#     print(type(data), type(sample_rate))
    #mfcc = librosa.feature.mfcc(y=data, sr=sample_rate)
#     librosa.display.specshow(mfcc, sr=sample_rate, x_axis='time')
    #mfccScaled = np.mean(mfcc.T, axis=0)
    print(data.shape)
    return data

def padding(array, xx, yy):
    """
    :param array: numpy array
    :param xx: desired height
    :param yy: desirex width
    :return: padded array
    """
    h = array.shape[0]
    w = array.shape[1]
    #print(h, w)
    a = (xx - h) // 2
    aa = xx - a - h
    b = (yy - w) // 2
    bb = yy - b - w
    print(h, w, xx, yy)
    return np.pad(array, pad_width=((a, aa), (b, bb)), mode='constant')

hop_length = 10 #the default spacing between frames
n_fft = 100

In [72]:

#def feature_gneration(audio_gen):
features = []
labels = []
viseme_set = list()
transcript_set = list()
words_list = []
viseme_text_features = []

viseme_feature_set = list()

for filename in os.listdir(read_viseme_mod):
    file_path_read = os.path.join(read_viseme_mod, filename)
#     print(file_path_read)
    f_r = open(file_path_read,'r+', encoding = 'utf-8-sig')
    root = read_bml(f_r)
    viseme_extract = read_viseme(root)
    f_split = filename.split("_")
    audio_session = f_split[0][4]
    if(len(f_split)==4):
        audio_file_dir = f_split[0]+"_"+f_split[1]+"_"+f_split[2]
    else:
        audio_file_dir = f_split[0]+"_"+f_split[1]
    audio_file_name = filename.split(".")[0]+".wav"
    audio_path = audio_dir + "/Session" + audio_session + "/sentences/wav/"+audio_file_dir+"/"+audio_file_name
#     print(f_r)
    if(1):
        for rec in viseme_extract:
            mfcc = create_mfcc(audio_path,float(rec[1]),float(rec[2])).tolist()
            #print(mfcc.shape, len(mfcc))
            #print(mfcc)
            labels.append(rec[0])
            features.append(mfcc)
        #viseme_feature_set.append(mfcc_)
    viseme_set.append(viseme_extract)
#     print(viseme_extract[len(viseme_extract)-1][2])
    transcript_set.append(read_transcript(root,viseme_extract[len(viseme_extract)-1][2]) )
for i, elem in enumerate(transcript_set):
    s = textual_features(transcript_set[i],viseme_set[i])
    viseme_text_features.append(s)
    
#### For textual data
csv_file_text = 'test_textual_feature_set_new.csv'
fo = open(csv_file_text,'a')
csv_write = csv.writer(fo)
for sent in viseme_text_features:
    for tup in sent:
        word_vec = model.wv[tup[1]]
        
        word_vec = word_vec.tolist()
        word_vec.append(tup[0])
        csv_write.writerows([word_vec])
    csv_write.writerow([0]*51)
    

C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[ 8.9127989e-04  1.4727926e-06 -1.0958598e-03 -1.1081063e-03
 -3.9790521e-04 -3.3714861e-04 -1.2562780e-03 -2.2449689e-03
 -2.5684454e-03 -2.2351667e-03 -1.4893352e-03 -6.3417392e-04
 -1.4091673e-04 -2.4249672e-04 -5.5186544e-04 -5.2544056e-04
 -1.3184182e-04  2.7669413e-04  5.9147994e-04  1.1074443e-03
  2.0231435e-03  2.9740750e-03  3.2901084e-03  2.8001191e-03
  2.1359844e-03  1.9577886e-03  2.1038901e-03  1.9609262e-03
  1.5221387e-03  1.4634928e-03  2.0947184e-03  2.7988546e-03
  2.7566468e-03  1.8537176e-03  6.6614145e-04 -1.1882389e-04
 -6.6988359e-05  8.2305557e-04  1.9132281e-03  2.1749518e-03
  1.2003550e-03 -6.3130072e-05 -1.4758884e-04  1.2048773e-03
  2.6540565e-03  2.8699213e-03  2.0020274e-03  1.0990052e-03
  5.7970069e-04  3.4359364e-05 -6.9896708e-04 -1.1721801e-03
 -1.2150022e-03 -1.4172323e-03 -2.2447931e-03 -3.1442372e-03
 -3.1412956e-03 -2.2062329e-03 -1.4596685e-03 -1.8624183e

128 15 128 50
(1, 128, 50)
128 4 128 50
(1, 128, 50)
128 6 128 50
(1, 128, 50)


C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-6.1244657e-04 -8.9851627e-04 -1.2065725e-03 -1.5156817e-03
 -1.7626394e-03 -1.8899461e-03 -1.7659843e-03 -1.2227076e-03
 -3.3726558e-04  4.2110705e-04  5.3215341e-04 -5.8489193e-05
 -8.7089615e-04 -1.3263396e-03 -1.1307320e-03 -2.9983112e-04
  8.8111794e-04  1.7971704e-03  1.7462268e-03  6.3399388e-04
 -6.9114275e-04 -1.2215646e-03 -9.4691868e-04 -8.3423709e-04
 -1.5382904e-03 -2.5671229e-03 -3.0287944e-03 -2.8323671e-03
 -2.6549043e-03 -2.8896653e-03 -3.1984192e-03 -3.1921845e-03
 -3.0636659e-03 -3.2495898e-03 -3.7398839e-03 -4.0575135e-03
 -3.8569479e-03 -3.3021986e-03 -2.8289056e-03 -2.6803818e-03
 -2.7366292e-03 -2.7185802e-03 -2.4693476e-03 -2.0359682e-03
 -1.5715761e-03 -1.2379141e-03 -1.1331150e-03 -1.1671139e-03
 -1.0307455e-03 -4.8467921e-04  2.7305167e-04  7.3147402e-04
  6.6315033e-04  3.9901340e-04  3.5956493e-04  5.2507268e-04
  6.1441486e-04  5.9982523e-04  6.6140993e-04  6.8569201e

128 15 128 50
(1, 128, 50)
128 10 128 50
(1, 128, 50)


C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-0.00705876 -0.00685421 -0.00645088 -0.00601696 -0.00566589 -0.00532146
 -0.00491381 -0.00456488 -0.00445285] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  data = np.array([padding(librosa.feature.mfcc(y_cut,
C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-0.00456203 -0.0046989  -0.00473442 -0.00470187 -0.00463939 -0.00446711
 -0.00410269 -0.00362953 -0.00325965 -0.00313622 -0.00321416 -0.00332735
 -0.00335232 -0.00331868 -0.00336526 -0.00356834 -0.00382504 -0.00395376
 -0.00390725 -0.00382039 -0.00382409 -0.00387795 -0.00383622 -0.00363643
 -0.00336354 -0.00314414 -0.00302893 -0.00298039 -0.00293457 -0.00285569
 -0.00274591 -0.00261924 -0.00247235 -0.00228395 -0.0020388  -0.00174436
 -0.00142965 -0.00113506 -0.00087989 -0.00061024 -0.00020936  0.00037069
  0.00098416  0.00137598  0.00143034] as keyword

...

128 5 128 50
(1, 128, 50)


C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[ 0.03461025  0.03995178  0.04618112  0.05229811  0.05746781  0.06064708
  0.06010478  0.05420035  0.04302835  0.02910062  0.01618486  0.00729679
  0.00337795  0.00331149  0.00495777  0.00644641  0.00693506  0.00643962
  0.00506821  0.00246319 -0.00203541 -0.00873798 -0.01711657 -0.02590069
 -0.03366175] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  data = np.array([padding(librosa.feature.mfcc(y_cut,


128 3 128 50
(1, 128, 50)


C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-3.94275039e-02 -4.28318232e-02 -4.36883457e-02 -4.15430479e-02
 -3.59662808e-02 -2.74872128e-02 -1.80375315e-02 -1.01620443e-02
 -5.79561247e-03 -5.84831648e-03 -1.04332818e-02 -1.85905341e-02
 -2.75620278e-02 -3.32002789e-02 -3.22265513e-02 -2.45922655e-02
 -1.34849483e-02 -2.72566453e-03  6.04512496e-03  1.38150314e-02
  2.21134964e-02  3.07009146e-02  3.73454131e-02  3.96356620e-02
  3.68003994e-02  3.00692488e-02  2.20171437e-02  1.58848111e-02
  1.48015302e-02  2.04055384e-02  3.14779282e-02  4.40574810e-02
  5.34906611e-02  5.70159443e-02  5.48871085e-02  4.93168868e-02
  4.24101576e-02  3.50021161e-02  2.71964949e-02  1.95564460e-02
  1.33738201e-02  9.75759141e-03  8.66707973e-03  8.83762538e-03
  8.45337007e-03  5.96841890e-03  7.42469565e-04 -6.73526712e-03
 -1.52565697e-02 -2.36821361e-02 -3.13725285e-02 -3.79579626e-02
 -4.29906249e-02 -4.59937565e-02 -4.66471016e-02 -4.47217412e-02
 

128 31 128 50
(1, 128, 50)


In [73]:
len(features)

3702

In [74]:
len(labels)

3702

In [75]:
len(viseme_text_features)

116

In [78]:
import pickle
pickle.dump(features, open('features_test.pkl', 'wb'))
pickle.dump(labels, open('labels_test.pkl', 'wb'))

In [43]:
feature_gneration(1)

C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-4.9183914e-03 -5.7762708e-03 -4.7722650e-03 -3.8439168e-03
 -3.6741849e-03 -3.4846086e-03 -2.9640552e-03 -2.4913030e-03
 -2.0860240e-03 -1.5916345e-03 -1.3113030e-03 -1.4575667e-03
 -1.6194504e-03 -1.4402263e-03 -1.1178888e-03 -8.3304720e-04
 -4.3581694e-04  4.3540647e-05  2.7625839e-04  1.8036809e-04
  4.3698205e-05  9.9127326e-05  3.4938299e-04  6.4228300e-04
  6.6368579e-04  1.7755221e-04 -5.2606466e-04 -8.1633870e-04
 -5.0747150e-04 -4.6619953e-05  1.7986125e-04  2.8286653e-04
  4.8399653e-04  6.8528851e-04  6.2738283e-04  2.7169136e-04
 -1.4612275e-04 -4.1244386e-04 -5.9798686e-04 -9.3760918e-04
 -1.4702943e-03 -2.0073161e-03 -2.5394477e-03 -3.3773794e-03
 -4.6297484e-03 -5.7675936e-03 -6.0626306e-03 -5.4188226e-03
 -4.5270664e-03 -4.1852952e-03 -4.5930496e-03 -5.2854102e-03
 -5.6271418e-03 -5.3311274e-03 -4.5590820e-03 -3.6426585e-03
 -2.8394992e-03 -2.3290105e-03 -2.1930204e-03 -2.2306934e

128 14 128 50
(1, 128, 50)
128 1 128 50
(1, 128, 50)
128 1 128 50
(1, 128, 50)
128 3 128 50
(1, 128, 50)
128 2 128 50
(1, 128, 50)


C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-0.00352344 -0.00411952 -0.00515133 -0.00580477 -0.00550638 -0.00468438
 -0.00423833 -0.00447309 -0.00498264 -0.00543338 -0.00583829 -0.00597278] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  data = np.array([padding(librosa.feature.mfcc(y_cut,
C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[-0.00526469 -0.00375111 -0.00256787 -0.00273553 -0.00374248 -0.00413752
 -0.00342899 -0.00253453 -0.00225782 -0.00225609 -0.00192974 -0.00150142
 -0.00148523 -0.00160342 -0.00108233  0.00012007] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  data = np.array([padding(librosa.feature.mfcc(y_cut,
C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[0.00113899 0.00136418 0.00118533 0.00131397 0.00180493 0.00217259] as keyword args. F

128 2 128 50
(1, 128, 50)
128 2 128 50
(1, 128, 50)
128 1 128 50
(1, 128, 50)
128 2 128 50
(1, 128, 50)
128 7 128 50
(1, 128, 50)


C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[ 5.10118064e-03  5.81760984e-03  7.08535407e-03  8.70033074e-03
  9.50418040e-03  8.84942431e-03  7.69338524e-03  7.47663015e-03
  8.28460790e-03  8.94542038e-03  8.79140850e-03  8.39029998e-03
  8.34558439e-03  8.25273246e-03  7.39135686e-03  5.87834325e-03
  4.50571533e-03  3.78572498e-03  3.74869700e-03  4.35725367e-03
  5.34622138e-03  5.77385584e-03  4.66259290e-03  2.40719225e-03
  8.24709306e-04  1.22519326e-03  2.80055171e-03  3.47298058e-03
  2.16943212e-03 -1.92145279e-04 -1.84854330e-03 -1.86141592e-03
 -6.71506627e-04  5.54131111e-04  9.60954872e-04  6.66450127e-04
  5.81467466e-04  1.47787901e-03  3.11269099e-03  4.28472413e-03
  3.82165262e-03  1.65398023e-03 -8.99403589e-04 -1.98794878e-03
 -7.88095756e-04  1.55627355e-03  2.84536439e-03  1.99567224e-03
  1.03319893e-04 -9.58371384e-04 -7.17761519e-04 -3.68318317e-04
 -1.00716017e-03 -2.31194776e-03 -3.18273623e-03 -3.10872379e-03
 

...

C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py:8: FutureWarning: Pass y=[ 0.03037344  0.02996258  0.02941882  0.0301787   0.03220197  0.03434811
  0.03552033  0.03518453  0.03337424  0.03085912  0.02908055  0.02915571
  0.03060717  0.03130876  0.02900092  0.02307894  0.01512409  0.0078121
  0.00313484  0.0013239   0.00118786  0.00132992  0.00110055  0.00072421
  0.00092373  0.00246651  0.0056382   0.0096719   0.01264051  0.01236404
  0.00806171  0.00147148 -0.00386456 -0.00500203 -0.00174123  0.00348811
  0.00782392  0.00999359  0.01046878  0.01037161  0.01064685  0.01174823
  0.01321796  0.01349309  0.01093478  0.00559256 -0.0003602  -0.0043602 ] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  data = np.array([padding(librosa.feature.mfcc(y_cut,
C:\Users\ratho\anaconda3\lib\site-packages\librosa\util\decorators.py:88: UserWarning: n_fft=100 is too small for input signal of length=48
  return f(*args, **kwargs)
C:\User

128 5 128 50
(1, 128, 50)
128 18 128 50
(1, 128, 50)


ERROR:root:Internal Python error in the inspect module.
Below is the traceback from this internal error.



Traceback (most recent call last):
  File "C:\Users\ratho\anaconda3\lib\site-packages\IPython\core\interactiveshell.py", line 3444, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/3100766619.py", line 1, in <module>
    feature_gneration(1)
  File "C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/1285629580.py", line 21, in feature_gneration
    mfcc = create_mfcc(audio_path,float(rec[1]),float(rec[2])).tolist()
  File "C:\Users\ratho\AppData\Local\Temp/ipykernel_13544/2491051015.py", line 4, in create_mfcc
    y, sr = librosa.load(audio_path,sr=28000)
  File "C:\Users\ratho\anaconda3\lib\site-packages\librosa\util\decorators.py", line 88, in inner_f
    return f(*args, **kwargs)
  File "C:\Users\ratho\anaconda3\lib\site-packages\librosa\core\audio.py", line 183, in load
    y = resample(y, orig_sr=sr_native, target_sr=sr, res_type=res_type)
  File "C:\Users\ratho\anaconda3\lib\site-packages\librosa\util\decor

TypeError: object of type 'NoneType' has no len()